In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import json

# Baseline

In [2]:
df = pd.read_csv("train.csv")  # taken directly from jupyter home

In [3]:
valid=pd.read_csv("validation.csv")
valid = valid.drop('timestamp', 1)


In [6]:
t1=df.values

In [7]:
t2=valid.values

In [15]:
train=np.concatenate((t1, t2), axis=0)

In [20]:
N=len(train)

In [393]:
mean = np.mean(train[:,2])
#mean=0
print(mean)
a=np.zeros(9970)
b=np.zeros(9998)

for l in range (0,1):
    for i in range (0,N):
        j=int(train[i,0])
        k=int(train[i,1])
        #mean=mean+0.01*(data[i,2]-mean-a[j]-b[k])
        a[j]=a[j]+0.01*(train[i,2]-mean-a[j]-b[k])
        b[k]=b[k]+0.01*(train[i,2]-mean-a[j]-b[k]) #continous update
        
#print(mean)
print(a)
print(b)

3.2034536683691477
[ 0.          0.4987188   0.8149613  ...  0.06961088 -0.12498166
  0.78761611]
[ 0.48495977 -0.36269839 -0.27436113 ...  0.          0.
  0.        ]


# Doing Prediction

In [221]:
df1 = pd.read_csv("test.csv")
test=df1.values
M=len(test)
prediction=np.zeros(M)
for i in range (0,M):
    j=int(test[i,0])
    k=int(test[i,1])
    prediction[i]=mean+a[j]+b[k]

In [406]:
p=0
for i in range (0,M):
    if ((prediction[i]>5) ):
        p=p+1
        prediction[i]=5
    if(prediction[i]<0.5):
        p=p+1
        prediction[i]=0.5
#print(p)

In [200]:
array=np.arange(0,M,1)
df2=pd.DataFrame(array,columns = ['Id'])
df2['Prediction'] = prediction




#numpy.savetxt(".csv", a, delimiter=",")
df2.to_csv('base.csv',index=False)

# PCA +Linear regression

In [36]:
genome_scores_df=pd.read_csv('genome_scores.csv') # Large (500MB)


In [247]:
train_df = pd.concat([df,valid])
#train_df = df

In [248]:
X=np.zeros((9998,1128)) 
movies_with_featvecs=set(genome_scores_df['movieId'])
# The average rating, for each of the movies in the training set. 
# -1 if it is not in the train set.
rating_movies = -1*np.ones(9998) 

for i in range(9998):
    if i not in movies_with_featvecs:
        continue
    temp = genome_scores_df[genome_scores_df['movieId']==i]
    feat_vec= np.array(temp['relevance'])
    X[i,:]=feat_vec

for i in range(9998):
    temp = train_df[train_df['movieId']==i]
    if len(temp)==0:
        continue
    ratings_curr_movies = temp['rating']
    rating_movies[i] = np.mean(ratings_curr_movies)
    

In [113]:
from sklearn import linear_model
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA

In [249]:
X_train = X[rating_movies>0]
Y_train = rating_movies[rating_movies>0]

In [251]:
pca = PCA(.90)
  
X_train1 = pca.fit_transform(X_train) 


In [405]:
# create linear regression object 
reg = linear_model.LinearRegression() 
  
# train the model using the training sets 
reg.fit(X_train1, Y_train) 
  
# regression coefficients 
#print('Coefficients: \n', reg.coef_) 
  
# variance score: 1 means perfect prediction 
#print('Variance score: {}'.format(reg.score(X_test, Y_test))) 

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None,
         normalize=False)

In [399]:
#X3=sc.transform(X)
X1 = pca.transform(X) 
X2 = reg.predict(X1) 

# pred

In [ ]:
Model=np.zeros(M)
for i in range(M):
    j=test[i,1]
    Model[i]=X2[j]
    

In [ ]:
p=0
for i in range (0,M):
    if ((Model[i]>5) ):
        p=p+1
        Model[i]=5
    if(Model[i]<0.5):
        p=p+1
        Model[i]=0.5
#print(p)

In [383]:
array=np.arange(0,len(test),1)
df2=pd.DataFrame(array,columns = ['Id'])
df2['Prediction'] = Model

#numpy.savetxt(".csv", a, delimiter=",")
df2.to_csv('regression.csv',index=False)

# One more regression based on user

In [12]:



from sklearn.linear_model import RidgeCV


train_data = pd.read_csv('train.csv')
test_data = pd.read_csv('test.csv')
genome_scores =  pd.read_csv('genome_scores.csv')

movie_attributes = {}
regressor = {}

group_movies = genome_scores.groupby('movieId')

for movie, df in group_movies:
    movie_attributes[movie] = df['relevance'].values
    


'''

prediction = np.zeros(len(ntest))
iteration = 0
    
for k in ntest:
    if k[0] in users:    
        ind7 = np.where(scores == k[1])
        X_test = scores[ind7,2].reshape(1,1128)
        prediction[iteration] = (regressors[int(k[0])]).predict(X_test)
        
    else:
        prediction[iteration] = 3.36
        
    iteration = iteration + 1
            
 '''   
alpha = np.arange(0.1,10,1)

group_users = train_data.groupby('userId')

for user, df in group_users:
    Y = np.array(df['rating'])
    X = []
    movie_array = np.array(df['movieId']).astype(int)
    delete_array = []
    for i in range(len(movie_array)):
        if movie_array[i] in movie_attributes:
            X.append(movie_attributes[movie_array[i]])
        else:
            delete_array.append(i)
    Y = np.delete(Y, delete_array)
    regressor[user] = RidgeCV(alphas = alpha).fit(X, Y)
    

    

In [17]:

nscores = genome_scores.values
ntrain = train_data.values
test=test_data.values
M=len(test)

movies_g = np.unique(nscores[:,0])
users = np.unique(ntrain[:,0])
AGAIN=np.zeros(M)
for l in range(M):
    k=test[l,0]
    m = test[l,1]
    if k in users:
        if m in movies_g:
            movie = movie_attributes[test[l,1]]
            movie = movie.reshape((1,1128))
            #print(k)
            AGAIN[l]=regressor[int(k)].predict(movie)


11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
11
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
14
1

40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
40
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
44
4

140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
140
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
141
142
142
142
142
142
142
142
142
142


193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
193
202
202
202
202
202
202
202
202
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206
206


240
240
240
240
240
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
243
244
244
244
244
244
244
244
244
244
244
244
244
244
244
244
244
244
244


...

9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9820
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823
9823


9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9867
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868
9868


9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899
9899


9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9939
9941
9941
9941
9941
9941
9941
9941
9941
9941
9941
9941
9941
9941
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944
9944


9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9954
9955
9955
9955
9955
9955
9955
9955
9955
9955
9955
9955
9955
9955
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959
9959


In [20]:
sub_df=pd.read_csv('base.csv')

pred_df=pd.read_csv('regression.csv')

In [21]:
sub=sub_df.values
pred1=pred_df.values

In [31]:
done=AGAIN
for l in range(M):
    if AGAIN[l]==0:
        done[l]=0.7*pred1[l,1]+0.3*sub[l,1]
    else:
        done[l]=0.27*sub[l,1]+0.5*pred1[l,1]+0.23*AGAIN[l]


In [32]:
p=0
for i in range (0,M):
    if ((done[i]>5) ):
        p=p+1
        done[i]=5
    if(done[i]<0.5):
        p=p+1
        done[i]=0.5
print(p)

0


In [33]:
array=np.arange(0,len(test),1)
df2=pd.DataFrame(array,columns = ['Id'])
df2['Prediction'] = done

df2.to_csv('user.csv',index=False)